In [1]:
#limpio la memoria
rm(list=ls())
gc()

#cargo librerias
library("data.table")
library("ROCR")
library("rpart")
library("rpart.plot")
library("caret")

used    (Mb) gc trigger (Mb) max used (Mb)
Ncells  560245 30.0 1165498    62.3 1165498  62.3
Vcells 1013112  7.8 8388608    64.0 1650267  12.6

Loading required package: lattice

Loading required package: ggplot2



In [53]:

#Parametros entrada

#kcarpeta_datasets    <- "../input/laboratorio-de-implementacion-i-2021/"   #KAGGLE
kcarpeta_datasets    <- "C:/Users/Jonathan/Desktop/MCD - Laboratorio/7.Labo_1/datasetsOri"                          #VM o Ubuntu

#Archivo con datos etiquetados para entrenamiento
karchivo_entrada      <-  paste0(kcarpeta_datasets, "/paquete_premium_202011.csv")

#Archivo con datos sin etiquetar para generar la predicción
karchivo_predecir      <-  paste0(kcarpeta_datasets, "/paquete_premium_202101.csv")

#Formato para submit en Kaggle
#karchivo_score      <-  "../input/uamds2020ldi1f1/Sample_201910_Fase_I.txt"

#Separador de campos en archivos
kcampos_separador     <-  "\t"

#Campo que identifica las muestras
kcampo_id             <-  "numero_de_cliente"

#Campo que contiene la clase a estimar
kclase_nomcampo       <-  "clase_ternaria"

#Valor de interés
kclase_valor_positivo <-  "BAJA+2"

#Campos a borrar para el entrenamiento
kcampos_a_borrar      <-  c(kcampo_id,kclase_nomcampo,"foto_mes")

#Campo que contendrá a la variable objetivo generada
kobjetivo             <-  "clase"

#Identificación del modelo
kmodelo               <-  "02-RPART"

#Ganancia por TP
kTPGain               <-  48750

#Pérdida por FP
kFPGain               <-  -1250

kSeed <- 130007


#Establezco semilla aleatoria
set.seed(kSeed)



In [54]:
#cargo los datos
dataset <- fread(karchivo_entrada)
dataset

#Para hacer pruebas rapidas puedo reducir el dataset a una fraccion
#subsample <- sample(1:nrow(dataset), .1 * nrow(dataset))
#dataset <- dataset[subsample,]

numero_de_cliente foto_mes active_quarter cliente_vip internet
1      4572266           202011   1              0           0       
2      4572285           202011   1              0           0       
3      4572379           202011   1              0           0       
4      4572571           202011   1              0           0       
5      4572624           202011   1              0           0       
6      4572759           202011   1              0           0       
7      4572819           202011   1              0           0       
8      4572850           202011   1              0           0       
9      4572919           202011   1              0           0       
10     4572988           202011   1              0           0       
11     4573051           202011   1              0           0       
12     4573083           202011   1              0           0       
13     4573246           202011   1              0           0       
14     4573642           202011   1              0           0       
15     4573764           202011   1              0           0       
16     4573849           202011   1              0           0       
17     4574141           202011   1              0           0       
18     4574264           202011   1              0           0       
19     4574368           202011   1              0           0       
20     4574562           202011   1              0           0       
21     4574597           202011   1              0           0       
22     4574685           202011   1              0           3       
23     4574820           202011   1              0           0       
24     4574861           202011   1              0           0       
25     4574905           202011   1              0           0       
26     4574964           202011   1              0           0       
27     4575213           202011   1              0           0       
28     4575401           202011   1              0           0       
29     4575542           202011   1              0           0       
30     4575681           202011   1              0           0       
...    ...               ...      ...            ...         ...     
238579 61031023          202011   1              0           0       
238580 61032311          202011   0              0           0       
238581 61034451          202011   0              0           0       
238582 61038874          202011   0              0           0       
238583 61041227          202011   0              0           0       
238584 61042880          202011   1              0           0       
238585 61045679          202011   0              0           0       
238586 61046681          202011   1              0           0       
238587 61050784          202011   1              0           0       
238588 61052066          202011   1              0           0       
238589 61056411          202011   0              0           0       
238590 61060925          202011   1              0           0       
238591 61061104          202011   0              0           0       
238592 61061202          202011   0              0           0       
238593 61061387          202011   1              0           0       
238594 61063438          202011   0              0           0       
238595 61064085          202011   0              0           0       
238596 61066486          202011   1              0           0       
238597 61066542          202011   1              0           0       
238598 61101298          202011   1              0           0       
238599 61101480          202011   0              0           0       
238600 61133370          202011   0              0           0       
238601 61441004          202011   0              0           0       
238602 61442723          202011   0              0           0       
238603 61442798          202011   1              0           0       
238604 61443932  

In [55]:
dataset[,..kcampos_a_borrar]

numero_de_cliente clase_ternaria foto_mes
1      4572266           CONTINUA       202011  
2      4572285           CONTINUA       202011  
3      4572379           CONTINUA       202011  
4      4572571           CONTINUA       202011  
5      4572624           CONTINUA       202011  
6      4572759           CONTINUA       202011  
7      4572819           CONTINUA       202011  
8      4572850           CONTINUA       202011  
9      4572919           CONTINUA       202011  
10     4572988           CONTINUA       202011  
11     4573051           CONTINUA       202011  
12     4573083           CONTINUA       202011  
13     4573246           CONTINUA       202011  
14     4573642           CONTINUA       202011  
15     4573764           CONTINUA       202011  
16     4573849           CONTINUA       202011  
17     4574141           CONTINUA       202011  
18     4574264           CONTINUA       202011  
19     4574368           CONTINUA       202011  
20     4574562           CONTINUA       202011  
21     4574597           CONTINUA       202011  
22     4574685           CONTINUA       202011  
23     4574820           CONTINUA       202011  
24     4574861           CONTINUA       202011  
25     4574905           CONTINUA       202011  
26     4574964           CONTINUA       202011  
27     4575213           CONTINUA       202011  
28     4575401           CONTINUA       202011  
29     4575542           CONTINUA       202011  
30     4575681           CONTINUA       202011  
...    ...               ...            ...     
238579 61031023          CONTINUA       202011  
238580 61032311          CONTINUA       202011  
238581 61034451          CONTINUA       202011  
238582 61038874          CONTINUA       202011  
238583 61041227          CONTINUA       202011  
238584 61042880          CONTINUA       202011  
238585 61045679          CONTINUA       202011  
238586 61046681          CONTINUA       202011  
238587 61050784          CONTINUA       202011  
238588 61052066          CONTINUA       202011  
238589 61056411          CONTINUA       202011  
238590 61060925          CONTINUA       202011  
238591 61061104          CONTINUA       202011  
238592 61061202          CONTINUA       202011  
238593 61061387          CONTINUA       202011  
238594 61063438          CONTINUA       202011  
238595 61064085          CONTINUA       202011  
238596 61066486          CONTINUA       202011  
238597 61066542          CONTINUA       202011  
238598 61101298          CONTINUA       202011  
238599 61101480          CONTINUA       202011  
238600 61133370          CONTINUA       202011  
238601 61441004          CONTINUA       202011  
238602 61442723          CONTINUA       202011  
238603 61442798          CONTINUA       202011  
238604 61443932          CONTINUA       202011  
238605 61444262          CONTINUA       202011  
238606 61444909          CONTINUA       202011  
238607 61446292          CONTINUA       202011  
238608 61446672          CONTINUA       202011

In [60]:
dataset[,(kcampos_a_borrar)]

[1] "numero_de_cliente" "clase_ternaria"    "foto_mes"

In [61]:
#Genero la clase
dataset[,(kobjetivo) := as.integer(dataset[,..kclase_nomcampo] == kclase_valor_positivo)] 

# NOTAS
# Los dos puntos en ..kclase_nomcampo buscan dentro de las variables del data.table a la que tenga el nombre asignado a kclase_nomcampo 
#(tb se podría haber usado dataset[,"clase_ternaria"] o dataset[,.(clase_ternaria)]. En todos los casos devuelve la columna del 
# dataset que se llama clase_ternaria. Dato: .() es un alias de list().
# Hacer dataset[,clase_ternaria] devuelve un vector (no una columna).

#Limpio campos a borrar
dataset[ ,  (kcampos_a_borrar) := NULL    ] 

#Completo missings
dataset[is.na(dataset)] <- 0

Warning message in `[.data.table`(dataset, , ..kclase_nomcampo):
"Both 'kclase_nomcampo' and '..kclase_nomcampo' exist in calling scope. Please remove the '..kclase_nomcampo' variable in calling scope for clarity."


In [65]:
# generacion del modelo
formula  <-  formula(paste(kobjetivo, "~ ."))
formula

clase ~ .

In [70]:
#Genero los 5 folds
folds <- createFolds(dataset$clase, 5, returnTrain = TRUE)
folds

$Fold1
    [1]      1      2      3      4      5      6      7      8      9     10
   [11]     11     12     13     14     16     17     19     20     22     23
   [21]     24     25     26     28     29     30     31     32     33     34
   [31]     35     36     37     38     39     40     41     43     44     45
   [41]     47     48     49     50     51     52     53     54     55     56
   [51]     58     60     61     62     63     64     65     66     67     68
   [61]     69     70     71     72     73     74     76     77     78     79
   [71]     81     82     83     84     85     86     87     88     89     90
   [81]     91     92     93     94     98    100    101    103    104    106
   [91]    107    108    109    110    111    113    114    115    116    117
  [101]    118    119    120    121    122    123    124    125    126    127
  [111]    128    129    130    132    133    135    136    138    139    140
  [121]    142    143    144    146    147    148    151    152    153    155
  [131]    156    157    158    159    160    162    163    164    165    166
  [141]    167    168    169    171    172    173    175    176    177    178
  [151]    180    181    182    183    184    185    189    190    191    192
  [161]    193    194    195    196    198    199    200    202    203    204
  [171]    206    207    208    209    210    211    212    214    215    216
  [181]    217    220    222    223    224    227    228    229    231    232
  [191]    233    234    235    236    237    238    239    240    242    243
  [201]    245    246    247    248    250    251    252    253    254    255
  [211]    256    257    258    259    260    262    264    265    266    267
  [221]    268    270    272    273    274    275    276    279    280    281
  [231]    282    283    284    286    287    288    289    291    293    294
  [241]    295    296    297    298    300    302    303    304    306    307
  [251]    308    310    311    313    314    316    319    320    321    322
  [261]    323    324    325    328    329    330    332    333    334    335
  [271]    336    337    338    340    341    342    343    344    346    347
  [281]    349    351    352    355    356    357    358    359    360    361
  [291]    362    364    367    368    369    370    371    372    373    375
  [301]    377    378    379    380    381    383    384    385    386    387
  [311]    389    390    391    392    393    394    395    396    399    400
  [321]    401    402    403    405    406    408    410    411    412    413
  [331]    414    415    416    418    419    421    422    423    424    426
  [341]    427    428    430    431    432    433    434    435    436    438
  [351]    439    441    443    445    446    447    448    450    452    453
  [361]    454    455    456    457    458    459    460    461    462    463
  [371]    464    466    467    468    469    470    471    472    473    475
  [381]    476    477    479    480    481    482    483    485    486    487
  [391]    488    490    491    493    494    495    496    497    498    499
  [401]    500    501    502    503    504    506    507    508    509    510
  [411]    512    513    514    515    517    518    519    520    522    523
  [421]    524    525    526    527    528    529    530    531    532    534
  [431]    536    537    538    539    540    541    543    545    546    547
  [441]    548    551    552    554    555    556    557    560    561    562
  [451]    563    564    565    567    568    569    570    571    572    573
  [461]    574    575    576    577    578    579    580    581    582    583
  [471]    584    585    587    588    590    591    593    594    595    596
  [481]    597    598    599    600    601    602    603    604    605    606
  [491]    607    608    609    610    611    612    613    614    615    616
  [501]    617    619    622    623    624    625    628    630    631    632
  [511]    634 

In [76]:
unlist(folds[paste0('Fold',1)]) # para que no aparezcan los nombres de cada linea (Fold11...Fold1123)
                                # usar el argumento use.names=FALSE dentro de la funcion unlist


[1]      1      2      3      4      5      6      7      8      9     10
   [11]     11     12     13     14     16     17     19     20     22     23
   [21]     24     25     26     28     29     30     31     32     33     34
   [31]     35     36     37     38     39     40     41     43     44     45
   [41]     47     48     49     50     51     52     53     54     55     56
   [51]     58     60     61     62     63     64     65     66     67     68
   [61]     69     70     71     72     73     74     76     77     78     79
   [71]     81     82     83     84     85     86     87     88     89     90
   [81]     91     92     93     94     98    100    101    103    104    106
   [91]    107    108    109    110    111    113    114    115    116    117
  [101]    118    119    120    121    122    123    124    125    126    127
  [111]    128    129    130    132    133    135    136    138    139    140
  [121]    142    143    144    146    147    148    151    152    153    155
  [131]    156    157    158    159    160    162    163    164    165    166
  [141]    167    168    169    171    172    173    175    176    177    178
  [151]    180    181    182    183    184    185    189    190    191    192
  [161]    193    194    195    196    198    199    200    202    203    204
  [171]    206    207    208    209    210    211    212    214    215    216
  [181]    217    220    222    223    224    227    228    229    231    232
  [191]    233    234    235    236    237    238    239    240    242    243
  [201]    245    246    247    248    250    251    252    253    254    255
  [211]    256    257    258    259    260    262    264    265    266    267
  [221]    268    270    272    273    274    275    276    279    280    281
  [231]    282    283    284    286    287    288    289    291    293    294
  [241]    295    296    297    298    300    302    303    304    306    307
  [251]    308    310    311    313    314    316    319    320    321    322
  [261]    323    324    325    328    329    330    332    333    334    335
  [271]    336    337    338    340    341    342    343    344    346    347
  [281]    349    351    352    355    356    357    358    359    360    361
  [291]    362    364    367    368    369    370    371    372    373    375
  [301]    377    378    379    380    381    383    384    385    386    387
  [311]    389    390    391    392    393    394    395    396    399    400
  [321]    401    402    403    405    406    408    410    411    412    413
  [331]    414    415    416    418    419    421    422    423    424    426
  [341]    427    428    430    431    432    433    434    435    436    438
  [351]    439    441    443    445    446    447    448    450    452    453
  [361]    454    455    456    457    458    459    460    461    462    463
  [371]    464    466    467    468    469    470    471    472    473    475
  [381]    476    477    479    480    481    482    483    485    486    487
  [391]    488    490    491    493    494    495    496    497    498    499
  [401]    500    501    502    503    504    506    507    508    509    510
  [411]    512    513    514    515    517    518    519    520    522    523
  [421]    524    525    526    527    528    529    530    531    532    534
  [431]    536    537    538    539    540    541    543    545    546    547
  [441]    548    551    552    554    555    556    557    560    561    562
  [451]    563    564    565    567    568    569    570    571    572    573
  [461]    574    575    576    577    578    579    580    581    582    583
  [471]    584    585    587    588    590    591    593    594    595    596
  [481]    597    598    599    600    601    602    603    604    605    606
  [491]    607    608    609    610    611    612    613    614    615    616
  [501]    617    619    622    623    624    625    628    630    631    632
  [511]    634    635    6

In [94]:
set.seed(1345)
#Genero los 5 folds
folds <- createFolds(dataset$clase, 5, returnTrain = TRUE)

#Inicializo ganancia
ganancia_total <- 0


for (fold in c(1,2,3,4,5))
{

#Selecciono los registros train/test para cada fold
train <- dataset[unlist(folds[paste0('Fold',fold)]),] # unlist: para transformar una lista en un vector
test <- dataset[-unlist(folds[paste0('Fold',fold)]),]
    
#Entreno el modelo
modelo   <-  rpart(formula,   data = train, maxdepth = 5,  cp=0,   xval=0)   

#Aplico al set de test
predicted <- predict(modelo, test) # predicted values

#Calculo ganancia sobre dataset de pruebas
test$score <- predicted
test$Predicted <- test$score > 0.025

#calculo la ganancia de incentivar cada caso
test[  , ganancia:= kFPGain ] #-1250 # creamos la variable "ganancia" dentro del dataset test
test[ clase==1,   ganancia:= kTPGain] #48750 # cambiamos la ganancia para los casos en que clase ==1 (los que predijimos que son BAJA+2)

#Determino ganancia
print(paste("La Ganancia Fold:",fold, 5*sum(test$Predicted*test$ganancia)))
ganancia_total <- ganancia_total + sum(test$Predicted*test$ganancia)   
    
}
print(paste("La Ganancia Total:",ganancia_total))

[1] "La Ganancia Fold: 1 9137500"
[1] "La Ganancia Fold: 2 7337500"
[1] "La Ganancia Fold: 3 8743750"
[1] "La Ganancia Fold: 4 7300000"
[1] "La Ganancia Fold: 5 5912500"
[1] "La Ganancia Total: 7686250"


In [90]:
#funcion que entrena/evalua ganancia para un fold
calculo_ganancia <-function(){
modelo   <-  rpart(formula,   data = train, maxdepth = 5,  cp=0,   xval=0)   

predicted <- predict(modelo, test) # predicted values

#Calculo ganancia sobre dataset de pruebas
test$score <- predicted
test$Predicted <- test$score > 0.025

#calculo la ganancia de incentivar cada caso
test[  , ganancia:= kFPGain ] #-1250
test[ clase==1,   ganancia:= kTPGain] #48750
    
return(sum(test$Predicted*test$ganancia))
    }

In [91]:
#Numero de semilla que estoy probando
i <- 0

#Inicializo ganancias CV
ganancia_total_cv <- list()

#Inicializo ganancias Train/Test
ganancia_total_tt <- list()


for (seed in c(21023, 39761,20707,2049,7187,7207,9436519, 30689))
{
i <- i + 1

#Fija semilla    
set.seed(seed)

##### 5 Fold cross Validation ######
#Genero folds
folds <- createFolds(dataset$clase, 5, returnTrain = TRUE)
ganancia_total_cv[[i]] <- 0
for (fold in c(1,2,3,4,5))
{
#train_rows <- sample(1:nrow(dataset), .66 * nrow(dataset))
train <- dataset[unlist(folds[paste0('Fold',fold)]),]
test <- dataset[-unlist(folds[paste0('Fold',fold)]),]

#Determino ganancia
ganancia_total_cv[[i]]<- ganancia_total_cv[[i]] + calculo_ganancia()
  
}
#######

train_rows <- createDataPartition(dataset$clase, p = .66, list = FALSE)
ganancia_total_tt[[i]] <- 0
#train_rows <- sample(1:nrow(dataset), .66 * nrow(dataset))
train <- dataset[train_rows,]
test <- dataset[-train_rows,]
#Determino ganancia
ganancia_total_tt[[i]]<- ganancia_total_tt[[i]] + 3*calculo_ganancia()
  
}

In [92]:
ganancia_total_cv

[[1]]
[1] 6763750

[[2]]
[1] 6922500

[[3]]
[1] 7206250

[[4]]
[1] 7905000

[[5]]
[1] 7330000

[[6]]
[1] 7371250

[[7]]
[1] 6980000

[[8]]
[1] 7470000

In [93]:
ganancia_total_tt

[[1]]
[1] 8388750

[[2]]
[1] 12086250

[[3]]
[1] 7541250

[[4]]
[1] 9045000

[[5]]
[1] 6791250

[[6]]
[1] 6131250

[[7]]
[1] 6697500

[[8]]
[1] 6930000

In [97]:
# PRUEBA DAI CON XVAL=5 DENTRO DE RPART
set.seed(1345)

train_rows <- createDataPartition(dataset$clase, p = .66, list = FALSE)
train <- dataset[train_rows,]
test <- dataset[-train_rows,]

modelo <- rpart(formula,   data = train, maxdepth = 5,  cp=0,   xval=5)   

predicted <- predict(modelo, test) # predicted values

#Calculo ganancia sobre dataset de pruebas
test$score <- predicted
test$Predicted <- test$score > 0.025

#calculo la ganancia de incentivar cada caso
test[  , ganancia:= kFPGain ] #-1250
test[ clase==1,   ganancia:= kTPGain] #48750
    
sum(test$Predicted*test$ganancia)*5

[1] 1753750

In [98]:
sum(test$Predicted*test$ganancia)*5

[1] 8768750

In [101]:
cptable(modelo)

ERROR: Error in cptable(modelo): no se pudo encontrar la función "cptable"
